In [1]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import os
print(os.listdir(".."))

['test_RUL_FD001_100x50.json', 'train_RUL_FD001_100x50.json', '.DS_Store', 'newData', 'selectedModel', 'test_FD001_100x50.json', 'preprocessing', 'allData', 'train_FD001_100x50.json', 'networkModel', 'allData100']


In [2]:
import json
with open("service1906_1506.json") as of:
    data = json.load(of)

In [3]:
computes = [c for c in data.keys() if c!="timespan"]
variables = [v for v in data[computes[0]] if v!='index' and v!='arrJob_scheduling']

In [4]:
print(computes)
print(variables)

['compute-1-1', 'compute-1-10', 'compute-1-11', 'compute-1-12', 'compute-1-13', 'compute-1-14', 'compute-1-15', 'compute-1-16', 'compute-1-17', 'compute-1-18', 'compute-1-19', 'compute-1-2', 'compute-1-20', 'compute-1-21', 'compute-1-22', 'compute-1-23', 'compute-1-24', 'compute-1-25', 'compute-1-26', 'compute-1-27', 'compute-1-28', 'compute-1-29', 'compute-1-3', 'compute-1-30', 'compute-1-31', 'compute-1-32', 'compute-1-33', 'compute-1-34', 'compute-1-35', 'compute-1-36', 'compute-1-37', 'compute-1-38', 'compute-1-39', 'compute-1-4', 'compute-1-40', 'compute-1-41', 'compute-1-42', 'compute-1-43', 'compute-1-44', 'compute-1-45', 'compute-1-46', 'compute-1-47', 'compute-1-48', 'compute-1-49', 'compute-1-5', 'compute-1-50', 'compute-1-51', 'compute-1-52', 'compute-1-53', 'compute-1-54', 'compute-1-55', 'compute-1-56', 'compute-1-57', 'compute-1-58', 'compute-1-59', 'compute-1-6', 'compute-1-60', 'compute-1-7', 'compute-1-8', 'compute-1-9', 'compute-10-25', 'compute-10-26', 'compute-10-27

In [5]:
#Check empty array
def getEmptyArr(data, c):
    cObj = data[c]
    cDf = pd.DataFrame()
    cDf['compute'] = [c for _ in data['timespan']]
    cDf['timespan'] = data['timespan']
    for v in variables:
        vArr = np.array(cObj[v])
        if len(vArr)==0:
            print('c=', c)
            print('v=', v)
for c in computes:
    getEmptyArr(data, c)

c= compute-1-26
v= arrTemperature


In [6]:
def addTarget(cDf, predictedVar, predictedStep):
    cDf[target] = cDf[predictedVar].shift(-predictedStep)
    cDf.dropna(inplace=True)

In [7]:
def getComputeDf(data, c, predictedVar, predictedStep):
    cObj = data[c]
    cDf = pd.DataFrame()
    cDf['compute'] = [c for _ in data['timespan']]
    cDf['timespan'] = data['timespan']
    for v in variables:
        vArr = np.array(cObj[v])
        if len(vArr)==0:
            return None
        else:
            for i in range(len(vArr[0])):
                cDf[v+str(i)] = vArr[:, i]
    cDf['timespan'] = pd.to_datetime(cDf['timespan'])
    print(predictedVar)
    addTarget(cDf, predictedVar, predictedStep)
    return cDf

In [8]:
predictedVar = 'arrTemperature0'
target = predictedVar + "_target"
predictedSteps = 4
df = pd.concat([x for x in [getComputeDf(data, c, predictedVar, predictedSteps) for c in computes] if type(x)!="NoneType"])

arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTemperature0
arrTempe

In [9]:
df = df.reset_index().drop('index', axis=1)

print(df.head(2000))

          compute                  timespan arrTemperature0 arrTemperature1  \
0     compute-1-1 2019-06-09 00:00:00+00:00              73              59   
1     compute-1-1 2019-06-09 00:05:00+00:00              73              59   
2     compute-1-1 2019-06-09 00:10:00+00:00              73              59   
3     compute-1-1 2019-06-09 00:15:00+00:00              73              59   
4     compute-1-1 2019-06-09 00:20:00+00:00              73              59   
...           ...                       ...             ...             ...   
1995  compute-1-1 2019-06-15 22:15:00+00:00              42              35   
1996  compute-1-1 2019-06-15 22:20:00+00:00              42              35   
1997  compute-1-1 2019-06-15 22:25:00+00:00              42              35   
1998  compute-1-1 2019-06-15 22:30:00+00:00              42              35   
1999  compute-1-1 2019-06-15 22:35:00+00:00              42              35   

     arrTemperature2 arrCPU_load0 arrMemory_usage0 

In [10]:
features = [x for x in df.columns if x not in ['compute', 'timespan', 'arrTemperature0_target']]

In [11]:
features

['arrTemperature0',
 'arrTemperature1',
 'arrTemperature2',
 'arrCPU_load0',
 'arrMemory_usage0',
 'arrFans_health0',
 'arrFans_health1',
 'arrFans_health2',
 'arrFans_health3',
 'arrPower_usage0']

# Plot and see data distribution

In [ ]:
from matplotlib import pyplot as plt
import seaborn as sns

In [ ]:
def plotAttrDataOfId(data, compute, features):
    plt.figure(figsize=(30, 20))
    for i, v in enumerate(features):
        plt.subplot(10, 3, i+1)
        cDf = df[df['compute']==compute]
        plt.plot(cDf['timespan'], cDf[v])
        plt.title(v)
        plt.tight_layout()

In [ ]:
for x in np.random.randint(0, len(computes), 3):
    plotAttrDataOfId(df, computes[x], features)

In [ ]:
def plotDataDistribution(data, features):
    plt.figure(figsize=(30, 10))
    for i, v in enumerate(features):
        plt.subplot(3, 10, i+1)
        sns.distplot(list(data[v].values))
        plt.title(v)
    plt.tight_layout()

In [ ]:
plotDataDistribution(df, features)

# Generate sequences
May need to fill forward (time sampling)

In [12]:
X_dfs = []
y = []
numberOfSequences = 1
sequenceSteps = 100
# generate training data.
randSteps = [10, 30]
for randStep in randSteps:
    for compute in computes:
        cDf = df[df['compute']==compute]
    #     print(cDf)
        if(len(cDf) > sequenceSteps):
            print("rand step: ",randSteps)
            X_dfs.append(cDf.iloc[randStep:randStep+sequenceSteps])
            y.append(X_dfs[-1][target].values[-1])

rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [

rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [

rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [10, 30]
rand step:  [

In [13]:
print(len(X_dfs))
# print(X_dfs[0:465])

print(X_dfs[466:931])

932
[         compute                  timespan arrTemperature0 arrTemperature1  \
30   compute-1-1 2019-06-09 02:30:00+00:00              73              59   
31   compute-1-1 2019-06-09 02:35:00+00:00              73              59   
32   compute-1-1 2019-06-09 02:40:00+00:00              73              59   
33   compute-1-1 2019-06-09 02:45:00+00:00              72              57   
34   compute-1-1 2019-06-09 02:50:00+00:00              73              58   
..           ...                       ...             ...             ...   
125  compute-1-1 2019-06-09 10:25:00+00:00              73              59   
126  compute-1-1 2019-06-09 10:30:00+00:00              73              59   
127  compute-1-1 2019-06-09 10:35:00+00:00              73              59   
128  compute-1-1 2019-06-09 10:40:00+00:00              73              59   
129  compute-1-1 2019-06-09 10:45:00+00:00              73              59   

    arrTemperature2 arrCPU_load0 arrMemory_usage0 arrFans_

In [14]:
from sklearn.model_selection import train_test_split
X_train_dfs, X_test_dfs, y_train, y_test = train_test_split(X_dfs, y, test_size=0.33)

In [15]:
X_train_dfs = X_dfs[0:465]
X_test_dfs = X_dfs[466:931]
y_train = y[0:465]
y_test = y[466:931]

# Scale

In [16]:
# combine the training data to create a scaler
train_dfs = pd.concat(X_train_dfs)
print(train_dfs['arrTemperature0'].var(axis=0))

283.1682281875873


In [17]:
from sklearn.preprocessing import StandardScaler
scaler = StandardScaler().fit(train_dfs[features].values)
print([x for x in scaler.mean_])
print([x for x in scaler.var_])

temp = scaler.transform(X_train_dfs[311][features].values)

[53.80898924731183, 42.407827956989244, 14.708064516129033, 0.6228002956774195, 10.488774370156309, 8741.630107526882, 8656.145806451614, 8714.652258064516, 8664.79569892473, 60.957063172043014]
[283.16213854827146, 138.83453657255174, 11.17427904960111, 2.2500161705697233, 229.95256870460952, 4323265.067480633, 4165640.487127575, 4309862.319935761, 4210867.396970748, 757.6788784550147]


In [18]:
X_train = np.array([scaler.transform(item[features].values) for item in X_train_dfs])
X_test = np.array([scaler.transform(item[features].values) for item in X_test_dfs])

In [19]:
# for record in X_train

In [20]:
print(np.max(X_train))
print(np.min(X_train))
X_train_temp = [scaler.transform(item[features].values) for item in X_train_dfs]
for item in X_train_dfs:
    print (scaler.transform(item[features].values))

4.718075488229462
-2.0714782418592477
[[ 1.14046052  1.40816804  1.88223786  3.0904367  -0.12321781  0.20602172
   0.1145788   0.2867735   0.10974656  1.60005046]
 [ 1.14046052  1.40816804  1.88223786  3.11182595 -0.12218693  0.07135754
   0.14887588  0.08446338  0.10974656  1.60005046]
 [ 1.14046052  1.40816804  1.88223786  3.05608482 -0.12335527  0.20602172
   0.25176712  0.21933679  0.24619615  1.58869755]
 [ 1.14046052  1.40816804  1.88223786  3.17339973 -0.12541703  0.20602172
   0.25176712  0.21933679  0.31442095  1.57734463]
 [ 1.14046052  1.40816804  1.88223786  3.22710287 -0.12442051  0.17235567
   0.32036128  0.11818174  0.31442095  1.58869755]
 [ 1.14046052  1.40816804  2.18138871  3.12534391 -0.12057188  0.07135754
   0.1145788   0.08446338  0.10974656  1.60005046]
 [ 1.14046052  1.32329862  1.88223786  3.17330707 -0.11964409  0.10502358
   0.21747004  0.11818174  0.21208375  1.60005046]
 [ 1.14046052  1.40816804  1.88223786  3.25126945 -0.12198076  0.17235567
   0.21747004

[[-0.88005097 -1.05304518  0.3864836  -0.41510604 -0.54557025  0.00402545
   0.01168756 -0.01669167  0.00740936 -0.75000318]
 [-0.82062416 -1.05304518  0.68563445 -0.41510604 -0.54567334  0.00402545
   0.01168756  0.01702668  0.00740936 -0.75000318]
 [-0.88005097 -1.1379146   0.3864836  -0.41482804 -0.54532971  0.00402545
   0.01168756 -0.01669167  0.00740936 -0.75000318]
 [-0.88005097 -1.1379146   0.3864836  -0.41492071 -0.54560462  0.00402545
   0.01168756  0.01702668  0.00740936 -0.75000318]
 [-0.88005097 -1.1379146   0.3864836  -0.41510604 -0.54560462  0.00402545
   0.01168756  0.01702668  0.00740936 -0.75000318]
 [-0.88005097 -1.1379146   0.3864836  -0.41492071 -0.54563898  0.00402545
  -0.0569066  -0.01669167  0.00740936 -0.75000318]
 [-0.88005097 -1.1379146   0.3864836  -0.41482804 -0.54436756  0.00402545
   0.01168756  0.01702668  0.00740936 -0.75000318]
 [-0.88005097 -1.05304518  0.68563445 -0.41501337 -0.54577643  0.00402545
   0.01168756  0.01702668 -0.06081544 -0.73865027]


[[-0.70177054 -0.7135675   1.58308701 -0.40964339 -0.5197982  -0.93862383
  -0.9143336  -0.85965047 -0.9136254  -0.75000318]
 [-0.70177054 -0.7135675   1.58308701 -0.41242072 -0.51983256 -0.87129174
  -0.9143336  -0.85965047 -0.9136254  -0.70459152]
 [-0.70177054 -0.7135675   1.58308701 -0.41390271 -0.51983256 -0.93862383
  -0.9143336  -0.85965047 -0.9136254  -0.7613561 ]
 [-0.70177054 -0.7135675   1.58308701 -0.41445804 -0.51986692 -0.87129174
  -0.9143336  -0.92708718 -0.9136254  -0.7613561 ]
 [-0.70177054 -0.7135675   1.58308701 -0.41455071 -0.51983256 -0.93862383
  -0.9143336  -0.85965047 -0.9136254  -0.7613561 ]
 [-0.76119735 -0.7135675   1.58308701 -0.41473604 -0.51986692 -0.87129174
  -0.9143336  -0.85965047 -0.9136254  -0.75000318]
 [-0.70177054 -0.7135675   1.58308701 -0.41482804 -0.51983256 -0.87129174
  -0.9143336  -0.85965047 -0.9136254  -0.75000318]
 [-0.70177054 -0.7135675   1.58308701 -0.41510604 -0.51983256 -0.87129174
  -0.9143336  -0.85965047 -0.9136254  -0.7613561 ]


[[ 0.18963159  0.13512672 -1.10927066 -0.08575522  0.23119949  0.94667472
   1.00630288  0.96114054  0.99666892  0.850758  ]
 [ 0.24905839  0.13512672 -1.10927066 -0.0839959   0.22999679  0.81201054
  -0.0569066   0.85998548 -0.06081544  0.850758  ]
 [ 0.18963159  0.13512672 -1.10927066 -0.0817739   0.23099331  0.50901613
  -0.0569066   0.52280196 -0.06081544  0.850758  ]
 [ 0.24905839  0.13512672 -1.10927066 -0.08325523  0.23085586  0.61001427
   0.69762916  0.65767537  0.65554493  0.850758  ]
 [ 0.18963159  0.13512672 -1.10927066 -0.08547789  0.22951571  0.30701986
   0.32036128  0.32049185  0.31442095  0.850758  ]
 [ 0.24905839  0.13512672 -1.10927066 -0.08603322  0.22965316  0.81201054
   0.86911456  0.82626713  0.86021932  0.850758  ]
 [ 0.18963159  0.21999614 -1.10927066 -0.08575522  0.22937826  0.74467845
   0.69762916  0.72511207  0.65554493  1.16863965]
 [ 0.24905839  0.13512672 -1.10927066 -0.08751455  0.22996243  0.50901613
   0.32036128  0.55652031  0.14385895  0.86211091]


[[-0.34520969 -0.20435097 -1.40842151 -0.41492071 -0.47474865 -1.44361452
  -1.46308688 -1.46658081 -1.45942378 -0.70459152]
 [-0.4046365  -0.20435097 -1.40842151 -0.41492071 -0.47526409 -1.44361452
  -1.46308688 -1.46658081 -1.45942378 -0.68188569]
 [-0.4046365  -0.20435097 -1.40842151 -0.41492071 -0.475161   -1.47728056
  -1.46308688 -1.46658081 -1.42531138 -0.6932386 ]
 [-0.34520969 -0.20435097 -1.40842151 -0.41482804 -0.47533281 -1.47728056
  -1.46308688 -1.53401752 -1.45942378 -0.67053277]
 [-0.4046365  -0.20435097 -1.40842151 -0.41492071 -0.47526409 -1.44361452
  -1.46308688 -1.46658081 -1.42531138 -0.70459152]
 [-0.4046365  -0.20435097 -1.40842151 -0.41501337 -0.47536718 -1.47728056
  -1.46308688 -1.46658081 -1.45942378 -0.70459152]
 [-0.4046365  -0.20435097 -1.40842151 -0.41510604 -0.47519536 -1.47728056
  -1.46308688 -1.46658081 -1.45942378 -0.70459152]
 [-0.34520969 -0.20435097 -1.40842151 -0.41492071 -0.47529845 -1.44361452
  -1.46308688 -1.46658081 -1.45942378 -0.70459152]


[[-0.52349012 -0.7135675  -0.81011981 -0.41492071 -0.55611961 -1.37628243
  -1.36019564 -1.36542576 -1.35708658 -0.72729735]
 [-0.52349012 -0.62869807 -0.81011981 -0.41492071 -0.55611961 -1.37628243
  -1.36019564 -1.36542576 -1.35708658 -0.72729735]
 [-0.52349012 -0.7135675  -0.81011981 -0.41482804 -0.55605089 -1.37628243
  -1.32589856 -1.36542576 -1.35708658 -0.6932386 ]
 [-0.52349012 -0.7135675  -0.81011981 -0.41492071 -0.55608525 -1.37628243
  -1.36019564 -1.36542576 -1.32297418 -0.70459152]
 [-0.52349012 -0.7135675  -0.81011981 -0.41510604 -0.55505437 -1.37628243
  -1.36019564 -1.36542576 -1.35708658 -0.72729735]
 [-0.52349012 -0.7135675  -0.81011981 -0.41492071 -0.55601653 -1.37628243
  -1.36019564 -1.36542576 -1.35708658 -0.73865027]
 [-0.52349012 -0.7135675  -0.81011981 -0.41482804 -0.55605089 -1.37628243
  -1.32589856 -1.36542576 -1.35708658 -0.72729735]
 [-0.52349012 -0.7135675  -0.81011981 -0.41482804 -0.5559478  -1.37628243
  -1.36019564 -1.36542576 -1.35708658 -0.72729735]


[[ 1.55644818  1.74764573  0.3864836   3.16025111 -0.1995031   0.30701986
   0.32036128  0.32049185  0.31442095  1.63410921]
 [ 1.61587499  1.49303747  0.3864836   3.17969571 -0.20122123  0.3406859
   0.35465836  0.32049185  0.38264574  1.63410921]
 [ 1.55644818  1.83251515  0.3864836   3.21664024 -0.20496677  0.30701986
   0.35465836  0.32049185  0.31442095  1.63410921]
 [ 1.55644818  1.83251515  0.3864836   3.29886195 -0.19960619  0.30701986
   0.32036128  0.2867735   0.31442095  1.6227563 ]
 [ 1.55644818  1.83251515  0.3864836   3.12386258 -0.19929692  0.3406859
   0.35465836  0.32049185  0.38264574  1.63410921]
 [ 1.55644818  1.83251515  0.3864836   3.24367681 -0.1983004   0.30701986
   0.35465836  0.32049185  0.31442095  1.6227563 ]
 [ 1.55644818  1.83251515  0.3864836   3.12358458 -0.19984673  0.30701986
   0.35465836  0.32049185  0.34853335  1.6227563 ]
 [ 1.55644818  1.83251515  0.3864836   3.25321411 -0.19692589  0.30701986
   0.35465836  0.32049185  0.31442095  1.60005046]
 [

   0.56044084  0.52280196  0.55320774  1.52058005]]
[[ 1.49702138  0.81408209 -0.81011981  0.16424388  1.58797792  0.54268218
   0.59473792  0.55652031  0.58732014  1.50922713]
 [ 1.49702138  0.89895152 -0.81011981  0.15535458  1.58708449  0.61001427
   0.59473792  0.55652031  0.65554493  1.6227563 ]
 [ 1.49702138  0.89895152 -0.81011981  0.15822523  1.58732503  0.61001427
   0.66333208  0.55652031  0.65554493  1.46381547]
 [ 1.49702138  0.81408209 -0.81011981  0.17165119  1.58715321  0.61001427
   0.59473792  0.55652031  0.58732014  1.49787422]
 [ 1.49702138  0.89895152 -0.81011981  0.15424392  1.58711885  0.61001427
   0.66333208  0.55652031  0.58732014  1.60005046]
 [ 1.49702138  0.89895152 -0.81011981  0.1400773   1.58729066  0.54268218
   0.66333208  0.55652031  0.58732014  1.63410921]
 [ 1.49702138  0.89895152 -0.81011981  0.12915134  1.58722194  0.61001427
   0.66333208  0.55652031  0.58732014  1.61140338]
 [ 1.49702138  0.72921267 -0.81011981  0.14378062  1.58856209  0.61001427

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




[[1.91300904 1.91738457 1.88223786 0.15053993 1.51186445 0.54268218
  0.56044084 0.55652031 0.55320774 1.38434506]
 [1.85358223 1.91738457 1.88223786 0.14433662 1.51048994 0.54268218
  0.56044084 0.52280196 0.58732014 1.44110964]
 [1.91300904 2.002254   1.88223786 0.13850331 1.51048994 0.54268218
  0.56044084 0.52280196 0.58732014 1.40705089]
 [1.91300904 1.91738457 1.88223786 0.15442858 1.51059303 0.54268218
  0.56044084 0.52280196 0.55320774 1.44110964]
 [1.91300904 2.002254   1.88223786 0.15387325 1.51045558 0.54268218
  0.56044084 0.52280196 0.55320774 1.40705089]
 [1.91300904 1.91738457 1.88223786 0.14729927 1.51048994 0.54268218
  0.56044084 0.52280196 0.58732014 1.39569797]
 [1.85358223 1.91738457 1.88223786 0.15257725 1.51083357 0.54268218
  0.56044084 0.55652031 0.55320774 1.39569797]
 [1.91300904 2.002254   1.88223786 0.16452121 1.51048994 0.54268218
  0.56044084 0.52280196 0.55320774 1.40705089]
 [1.91300904 1.91738457 1.88223786 0.14776194 1.51268916 0.54268218
  0.5604408

In [21]:
y_train = np.array(y_train)
y_test = np.array(y_test)

In [22]:
sns.distplot(y_train)

NameError: name 'sns' is not defined

In [23]:
sns.distplot(y_test)

NameError: name 'sns' is not defined

In [24]:
print (len(y_train))
print (len(y_test))
print(y_train)
print(y_test)

465
465
[74 42 49 58 38 43 46 48 82 41 37 43 40 41 44 47 48 30 58 33 55 45 37 86
 48 33 34 76 39 31 80 36 79 81 71 46 66 81 58 73 37 78 34 36 66 36 81 36
 75 39 38 67 36 72 41 83 42 81 42 78 40 83 82 84 84 45 46 83 44 86 46 71
 37 80 40 72 82 40 79 44 34 83 38 35 77 38 39 59 79 39 44 80 69 38 37 38
 65 34 80 36 34 50 80 36 41 38 41 42 66 44 46 50 49 50 44 47 48 49 33 35
 76 38 37 45 78 38 39 43 48 48 47 50 50 53 44 55 47 51 34 37 46 44 50 46
 43 45 47 50 69 36 36 82 34 41 45 46 47 50 47 47 52 38 44 46 50 56 41 64
 45 44 74 41 80 43 45 72 35 36 38 43 47 49 49 80 65 82 67 50 48 54 56 34
 85 69 37 69 74 38 81 75 80 85 35 66 37 74 40 38 36 36 81 37 38 72 42 75
 46 43 48 47 59 50 74 38 59 82 70 35 80 74 57 69 83 68 63 72 39 77 34 40
 75 81 76 60 77 39 81 42 45 74 46 47 48 49 43 53 47 50 47 48 49 47 36 40
 78 39 37 33 77 85 86 40 83 77 45 41 38 43 65 83 33 33 77 81 43 40 77 43
 65 81 84 65 73 78 78 67 35 79 76 50 63 77 38 39 43 45 46 48 69 44 39 41
 69 40 44 45 38 35 37 74 40 80 22 58 81 47 

# Export data

In [25]:
from IPython.display import FileLink

In [26]:
import codecs, json

In [27]:
def exportNPArrayToJson(a, fileName):
    b = a.tolist()
    json.dump(b, codecs.open(fileName, 'w', encoding='utf-8'))

In [28]:
exportNPArrayToJson(X_train, 'X_train_HPCC_1_100.json')
exportNPArrayToJson(X_test, 'X_test_HPCC_1_100.json')
exportNPArrayToJson(y_train, 'y_train_HPCC_1_100.json')
exportNPArrayToJson(y_test, 'y_test_HPCC_1_100.json')

In [29]:
FileLink('X_train_HPCC_1_100.json')

/Users/haovan/Documents/HaoVanWorkspace/H/VCNN/data/preprocessing/X_train_HPCC_1_100.json

In [30]:
FileLink('X_test_HPCC_1_100.json')

/Users/haovan/Documents/HaoVanWorkspace/H/VCNN/data/preprocessing/X_test_HPCC_1_100.json

In [31]:
FileLink('y_train_HPCC_1_100.json')

/Users/haovan/Documents/HaoVanWorkspace/H/VCNN/data/preprocessing/y_train_HPCC_1_100.json

In [32]:
FileLink('y_test_HPCC_1_100.json')

/Users/haovan/Documents/HaoVanWorkspace/H/VCNN/data/preprocessing/y_test_HPCC_1_100.json

In [ ]:
FileLink('X_train_HPCC_1_100.json')
FileLink('X_train_HPCC_1_100.json')
FileLink('X_train_HPCC_1_100.json')
FileLink('X_train_HPCC_1_100.json')

In [ ]:
from keras import regularizers
from keras.models import Sequential
from keras.layers import LSTM
from keras.layers import Dense
from keras.layers import Activation
from keras.layers import Dropout
from keras.layers import Flatten

# from keras import backend as K
# K.set_session(K.tf.Session(config=K.tf.ConfigProto(intra_op_parallelism_threads=36, inter_op_parallelism_threads=36)))


def createModel(l1Nodes, l2Nodes, d1Nodes, d2Nodes, inputShape):
    # input layer
    lstm1 = LSTM(l1Nodes, input_shape=inputShape, return_sequences=True, kernel_regularizer=regularizers.l2(0.1))
    do1 = Dropout(0.2)
    
    lstm2 = LSTM(l2Nodes, return_sequences=True, kernel_regularizer=regularizers.l2(0.1))
    do2 = Dropout(0.2)
    
    flatten = Flatten()
    
    dense1 = Dense(d1Nodes, activation='relu')
    do3 = Dropout(0.2)
    
    dense2 = Dense(d2Nodes, activation='relu')
    do4 = Dropout(0.2)
    
    # output layer
    outL = Dense(1, activation='relu')
    # combine the layers
#     layers = [lstm1, do1, lstm2, do2, dense1, do3, dense2, do4, outL]
    layers = [lstm1, lstm2, flatten,  dense1, dense2, outL]
    # create the model
    model = Sequential(layers)
    model.compile(optimizer='adam', loss='mse')
    return model

In [ ]:
from keras.callbacks import ModelCheckpoint
from keras.callbacks import EarlyStopping
from keras.models import load_model
# ten fold
from sklearn.model_selection import StratifiedKFold
kfold = StratifiedKFold(n_splits=3, shuffle=True)
from keras.models import load_model
msescores = []
counter= 0



for trainIdx, testIdx in kfold.split(X_train, y_train):
    counter = counter + 1
    # create callbacks
    model_path = 'best_model_fold'+str(counter)+'.h5'
    mc = ModelCheckpoint(model_path, monitor='val_loss', mode='min', verbose=1, save_best_only=True)
    es = EarlyStopping(monitor='val_loss', min_delta=0, patience=3, verbose=1)
    # create model
    model = createModel(64, 64, 8, 8, (X_train.shape[1], X_train.shape[2]))
    model.fit(X_train[trainIdx], y_train[trainIdx], validation_data=(X_train[testIdx], y_train[testIdx]), batch_size=32, epochs=40, callbacks=[mc, es])
    # Done load the best model of this fold
    saved_model = load_model(model_path)
    msescores.append({'path': model_path, 'mse': saved_model.evaluate(X_train[testIdx], y_train[testIdx])})

In [ ]:
msescores

In [ ]:
for md in msescores:
    saved_model = load_model(md['path'])
    print(saved_model.evaluate(X_test, y_test))

In [ ]:
best_model = load_model(msescores[np.argmin([sc['mse'] for sc in msescores])]['path'])

In [ ]:
predicted = saved_model.predict(X_test)

In [ ]:
baseline = np.array([df[predictedVar].values[-1] for df in X_test_dfs])

In [ ]:
plt.figure(figsize=(50, 10))
plt.plot(range(50), predicted[:50], 'x', label='predicted')
plt.plot(range(50), baseline[:50], 'v', label='baseline')
plt.plot(range(50), y_test[:50], 'o', label='actual')
plt.legend()

In [ ]:
from sklearn.metrics import mean_squared_error
mse = mean_squared_error(y_test, predicted)
msebaseline = mean_squared_error(y_test, baseline)

In [ ]:
print('mse=', mse)
print('msebaseline=', msebaseline)

In [ ]:
from keras.models import Sequential

In [ ]:
model = Sequential()

In [ ]:
model.predict_classes

In [ ]:
print (X_train[0].mean())
print (scaler.mean_[0])
print (scaler.var_[0])

In [ ]:
from sklearn import preprocessing
print(train_dfs['arrTemperature0'])


In [ ]:
sc = StandardScaler().fit([[0,1], [1,2], [2,3], [3,4], [4,5], [1000002,13]])

In [ ]:
print(sc.mean_)
print(sc.var_)

In [ ]:
sc.transform([[0,1], [1,2], [2,3], [3,4], [4,5], [1000002,13]])

In [ ]:
sc_ = StandardScaler().fit([[-0.44721896, -0.92966968],
       [-0.44721628, -0.6761234 ],
       [-0.4472136 , -0.42257713],
       [-0.44721091, -0.16903085],
       [-0.44720823,  0.08451543],
       [ 2.23606798,  2.11288564]])

In [ ]:
print(sc_.mean_)
print(sc_.var_)